In [2]:
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
import json,argparse
import numpy as np
import pandas as pd
# plot the data
import matplotlib.pyplot as plt
import natsort
import os

In [3]:
df_dict_everything_ooo = {}
df_dict_everything_io = {}

def get_batch_pin_memory_time_with_ts(log_file: str) -> pd.DataFrame:
    with open(log_file) as f:
        lines = f.readlines()
        batch_pin_memory_times = {}
        batch_pin_memory_times_ts = {}
        
        for line in lines:
            if "SBatchPinMemory" in line:
                parts = line.split(',')
                batch_id = int(parts[0].split('_')[1])
                pin_memory_time = float(parts[-1]) / (1000 * 1000 * 1000)
                batch_pin_memory_times[batch_id] = pin_memory_time
                batch_pin_memory_times_ts[batch_id] = float(parts[-2])
        
        data = {
            'batch_id': list(batch_pin_memory_times.keys()),
            'pin_memory_time': list(batch_pin_memory_times.values()),
            'pin_memory_time_ts': list(batch_pin_memory_times_ts.values())
        }
        
        df = pd.DataFrame(data)
        df.set_index('batch_id', inplace=True)
        df.sort_index(inplace=True)
        
        return df

def get_batch_idle_times_with_ts(log_file: str) -> pd.DataFrame:
    with open(log_file) as f:
        lines = f.readlines()
        batch_wait_times = {}
        batch_wait_times_ts = {}
        
        for line in lines:
            if "SBatchWait" in line:
                parts = line.split(',')
                batch_id = int(parts[0].split('_')[1])
                batch_wait_times[batch_id] = float(parts[2]) / (1000 * 1000 * 1000)
                batch_wait_times_ts[batch_id] = float(parts[1])
        
        data = {
            'batch_id': list(batch_wait_times.keys()),
            'wait_time': list(batch_wait_times.values()),
            'wait_time_ts': list(batch_wait_times_ts.values())
        }
        
        df = pd.DataFrame(data)
        df.set_index('batch_id', inplace=True)
        df.sort_index(inplace=True)
        
        return df

def get_batch_preprocessing_times_with_ts(log_file: str) -> pd.DataFrame:
    with open(log_file) as f:
        lines = f.readlines()
        batch_preprocessing_times = {}
        batch_preprocessing_times_ts = {}
        
        for line in lines:
            if "SBatchPreprocessed" in line:
                parts = line.split(',')
                batch_id = int(parts[0].split('_')[1])
                preprocessing_time = float(parts[-1]) / (1000 * 1000 * 1000)
                batch_preprocessing_times[batch_id] = preprocessing_time
                batch_preprocessing_times_ts[batch_id] = float(parts[-2])
        
        data = {
            'batch_id': list(batch_preprocessing_times.keys()),
            'preprocessing_time': list(batch_preprocessing_times.values()),
            'preprocessing_time_ts': list(batch_preprocessing_times_ts.values())
        }
        
        df = pd.DataFrame(data)
        df.set_index('batch_id', inplace=True)
        df.sort_index(inplace=True)
        
        return df

def get_batch_consumed_times_with_ts(log_file: str) -> pd.DataFrame:
    with open(log_file) as f:
        lines = f.readlines()
    batch_consumed_times = {}
    batch_consumed_times_ts = {}
    for line in lines:
        if "SBatchConsumed" in line:
            parts = line.split(',')
            batch_id = int(parts[0].split('_')[1])
            consumed_time = float(parts[-1]) / (1000 * 1000 * 1000)
            batch_consumed_times[batch_id] = consumed_time
            batch_consumed_times_ts[batch_id] = int(parts[-2])
    
    data = {
        'batch_id': list(batch_consumed_times.keys()),
        'consumed_time': list(batch_consumed_times.values()),
        'consumed_time_ts': list(batch_consumed_times_ts.values())
    }
    
    df = pd.DataFrame(data)
    df.set_index('batch_id', inplace=True)
    df.sort_index(inplace=True)
    
    return df

def get_gpu_util_time(gpu_util_file: str) -> pd.DataFrame:
    util_times = []
    batch_id = 1

    with open(gpu_util_file) as f:
        for line in f:
            if "ms" in line:
                util_time = float(line.split()[0]) / 1000
                util_times.append((batch_id, util_time))
                batch_id += 1

    df = pd.DataFrame(util_times, columns=['batch_id', 'util_time'])
    df.set_index('batch_id', inplace=True)
    df.sort_index(inplace=True)

    return df

def get_gpu_wait_time(gpu_file: str) -> pd.DataFrame:
    idle_times = []
    batch_id = 1
    
    with open(gpu_file) as f:
        for line in f:
            if "ms" in line:
                idle_time = float(line.split()[0]) / 1000
                idle_times.append((batch_id, idle_time))
                batch_id += 1
    
    df = pd.DataFrame(idle_times, columns=['batch_id', 'idle_time'])
    df.set_index('batch_id', inplace=True)
    df.sort_index(inplace=True)
    
    return df

def get_everything(log_files, gpu_file, gpu_util_file):
    # get e2e time
    df_main = None
    for file in log_files:
        if "main" in file:
            # get the batch wait time by ID
            df_batch_wait_times = get_batch_idle_times_with_ts(file)
            # concat with df_main using batch_id
            if df_main is None:
                df_main = df_batch_wait_times
            else:
                df_main = df_main.combine_first(df_batch_wait_times)

            df_batch_consumed_times = get_batch_consumed_times_with_ts(file)
            # concat with df_main using batch_id
            if df_main is None:
                df_main = df_batch_consumed_times
            else:
                df_main = df_main.combine_first(df_batch_consumed_times)
            
            df_batch_pin_memory_times = get_batch_pin_memory_time_with_ts(file)
            # concat with df_main using batch_id
            if df_main is None:
                df_main = df_batch_pin_memory_times
            else:
                df_main = df_main.combine_first(df_batch_pin_memory_times)
            
        if "worker" in file:
            # get batch preprocessing time by ID
            df_batch_preprocessing_times = get_batch_preprocessing_times_with_ts(file)
            # concat with df_main using batch_id
            if df_main is None:
                df_main = df_batch_preprocessing_times
            else:
                df_main = df_main.combine_first(df_batch_preprocessing_times)
    # in df_main, calculate wait_time_ts - (preprocessing_time_ts + preprocessing_time) for each batch and store in a new column
    df_main['wait_time_preprocessing_time_ts_diff'] = df_main['wait_time_ts']/(1000 * 1000 * 1000) - (df_main['preprocessing_time_ts']/(1000 * 1000 * 1000) + df_main['preprocessing_time'])
    df_main['wait_time_preprocessing_time_ts_diff'] = df_main['wait_time_preprocessing_time_ts_diff']
    # in df_main, calculate (consumed_time_ts - (preprocessing_time_ts + preprocessing_time) prefor each batch and store in a new column
    df_main['consumed_time_preprocessing_time_ts_diff'] = df_main['consumed_time_ts']/(1000 * 1000 * 1000) - (df_main['preprocessing_time_ts']/(1000 * 1000 * 1000) + df_main['preprocessing_time'])
    df_main['consumed_time_preprocessing_time_ts_diff'] = df_main['consumed_time_preprocessing_time_ts_diff']
    # get the idle times
    # df_gpu = get_gpu_wait_time(gpu_file)
    # df_gpu_util = get_gpu_util_time(gpu_util_file)
    # concat with df_main using batch_id
    # df_main = pd.concat([df_main,df_gpu],axis=1)
    # df_main = df_main.combine_first(df_gpu)
    # df_main = df_main.combine_first(df_gpu_util)
    return df_main

In [4]:


# Define the directory to search for log files
dir_ooo = "../final_analysis_cloudlab_twenty"

# Function to get GPU and main log files from the specified directory
def get_gpu_and_main_log_files(dir_path: str) -> tuple:
    import os
    gpu_files = []  # List to store GPU idle files
    gpu_util_files = []  # List to store GPU utilization files
    log_files = {}  # Dictionary to store main and worker log files

    # Walk through the directory and its subdirectories
    for root, dirs, files in os.walk(dir_path):
        log_files[root] = []  # Initialize the list for the current directory
        for file in files:
            # Check if the file is a GPU utilization file (excluding PNG files)
            if "gpu_util" in file and 'png' not in file:
                gpu_util_files.append(os.path.join(root, file))
            # Check if the file is a GPU idle file (excluding PNG files)
            if "gpu_idle" in file and 'png' not in file:
                gpu_files.append(os.path.join(root, file))
            # Check if the file is a main log file (excluding PNG files)
            if "main" in file and 'png' not in file:
                log_files[root].append(os.path.join(root, file))
            # Check if the file is a worker log file (excluding PNG files)
            if "worker" in file and 'png' not in file:
                log_files[root].append(os.path.join(root, file))

    # Return the lists of GPU idle files, main and worker log files, and GPU utilization files
    return gpu_files, log_files, gpu_util_files

# Get the GPU idle files, main and worker log files, and GPU utilization files from the specified directory
gpu_files, log_files, gpu_util_files = get_gpu_and_main_log_files(dir_ooo)

# Filter out empty log file entries
log_files = {key: val for key, val in log_files.items() if val}

# Sort the log file keys naturally
log_files_keys = natsort.natsorted(log_files)

# Sort the GPU idle files naturally
gpu_files = natsort.natsorted(gpu_files)

# Sort the GPU utilization files naturally
gpu_util_files = natsort.natsorted(gpu_util_files)

for key, gpu_file, gpu_util_file in zip(log_files_keys, gpu_files, gpu_util_files):
    log_files_list = log_files[key]
    # keep only the text after the last '/'
    key = key.split('/')[-1]
    print(key)
    df_dict_everything_ooo[key] = get_everything(log_files_list, gpu_file, gpu_util_file)

b128_gpu2_w4
b128_gpu2_w8
b128_gpu2_w12
b128_gpu2_w16
b128_gpu2_w20
b128_gpu2_w24
b128_gpu2_w28
b128_gpu3_w4
b128_gpu3_w8
b128_gpu3_w12
b128_gpu3_w16
b128_gpu3_w20
b128_gpu3_w24
b128_gpu3_w28
b128_gpu4_w4
b128_gpu4_w8
b128_gpu4_w12
b128_gpu4_w16
b128_gpu4_w20
b128_gpu4_w24
b128_gpu4_w28
b256_gpu2_w4
b256_gpu2_w8
b256_gpu2_w12
b256_gpu2_w16
b256_gpu2_w20
b256_gpu2_w24
b256_gpu2_w28
b256_gpu3_w4
b256_gpu3_w8
b256_gpu3_w12
b256_gpu3_w16
b256_gpu3_w20
b256_gpu3_w24
b256_gpu3_w28
b256_gpu4_w4
b256_gpu4_w8
b256_gpu4_w12
b256_gpu4_w16
b256_gpu4_w20
b256_gpu4_w24
b256_gpu4_w28
b512_gpu2_w4
b512_gpu2_w8
b512_gpu2_w12
b512_gpu2_w16
b512_gpu2_w20
b512_gpu2_w24
b512_gpu2_w28
b512_gpu3_w4
b512_gpu3_w8
b512_gpu3_w12
b512_gpu3_w16
b512_gpu3_w20
b512_gpu3_w24
b512_gpu3_w28
b512_gpu4_w4
b512_gpu4_w8
b512_gpu4_w12
b512_gpu4_w16
b512_gpu4_w20
b512_gpu4_w24
b512_gpu4_w28
b1024_gpu2_w4
b1024_gpu2_w8
b1024_gpu2_w12
b1024_gpu2_w16
b1024_gpu2_w20
b1024_gpu2_w24
b1024_gpu2_w28
b1024_gpu3_w4
b1024_gpu3_w8
b1024

In [9]:


# Define the directory to search for log files
dir_io = "../lotustrace_result_priority"

# Function to get GPU and main log files from the specified directory
def get_gpu_and_main_log_files(dir_path: str) -> tuple:
    import os
    gpu_files = []  # List to store GPU idle files
    gpu_util_files = []  # List to store GPU utilization files
    log_files = {}  # Dictionary to store main and worker log files

    # Walk through the directory and its subdirectories
    for root, dirs, files in os.walk(dir_path):
        log_files[root] = []  # Initialize the list for the current directory
        for file in files:
            # Check if the file is a GPU utilization file (excluding PNG files)
            if "gpu_util" in file and 'png' not in file:
                gpu_util_files.append(os.path.join(root, file))
            # Check if the file is a GPU idle file (excluding PNG files)
            if "gpu_idle" in file and 'png' not in file:
                gpu_files.append(os.path.join(root, file))
            # Check if the file is a main log file (excluding PNG files)
            if "main" in file and 'png' not in file:
                log_files[root].append(os.path.join(root, file))
            # Check if the file is a worker log file (excluding PNG files)
            if "worker" in file and 'png' not in file:
                log_files[root].append(os.path.join(root, file))

    # Return the lists of GPU idle files, main and worker log files, and GPU utilization files
    return gpu_files, log_files, gpu_util_files

# Get the GPU idle files, main and worker log files, and GPU utilization files from the specified directory
gpu_files, log_files, gpu_util_files = get_gpu_and_main_log_files(dir_io)

# Filter out empty log file entries
log_files = {key: val for key, val in log_files.items() if val}

# Sort the log file keys naturally
log_files_keys = natsort.natsorted(log_files)

# Sort the GPU idle files naturally
gpu_files = natsort.natsorted(gpu_files)

# Sort the GPU utilization files naturally
gpu_util_files = natsort.natsorted(gpu_util_files)


# for key, gpu_file, gpu_util_file in zip(log_files_keys, gpu_files, gpu_util_files):
for key in log_files_keys:
    log_files_list = log_files[key]
    # keep only the text after the last '/'
    key = key.split('/')[-1]
    print(key)
    df_dict_everything_io[key] = get_everything(log_files_list, gpu_file, gpu_util_file)

b128_gpu1_w4
b128_gpu1_w8
b128_gpu1_w12
b128_gpu1_w16
b128_gpu1_w20
b128_gpu1_w24
b128_gpu1_w28
b128_gpu2_w4
b128_gpu2_w8
b128_gpu2_w12
b128_gpu2_w16
b128_gpu2_w20
b128_gpu2_w24
b128_gpu2_w28
b128_gpu3_w4
b128_gpu3_w8
b128_gpu3_w12
b128_gpu3_w16
b128_gpu3_w20
b128_gpu3_w24
b128_gpu3_w28
b128_gpu4_w4
b128_gpu4_w8
b128_gpu4_w12
b128_gpu4_w16
b128_gpu4_w20
b128_gpu4_w24
b128_gpu4_w28
b256_gpu1_w4
b256_gpu1_w8
b256_gpu1_w12
b256_gpu1_w16
b256_gpu1_w20
b256_gpu1_w24
b256_gpu1_w28
b256_gpu2_w4
b512_gpu4_w24
b512_gpu4_w28


In [16]:
import os
import matplotlib.pyplot as plt

# Ensure the output directory exists
output_dir = "figs/wait_times"
os.makedirs(output_dir, exist_ok=True)

# # Example structure of df_dict_everything (replace with actual data)
# df_dict_everything = {
#     'config1': pd.DataFrame({'wait_time': [0.5, 0.6, 0.7, 0.8]}),
#     'config2': pd.DataFrame({'wait_time': [0.4, 0.5, 0.6, 0.7]}),
#     'config3': pd.DataFrame({'wait_time': [0.3, 0.4, 0.5, 0.6]}),
# }

# Dictionary to store standard deviation for each configuration
std_dev_dict_ooo = {}

for key, df in df_dict_everything_ooo.items():
    print(f"Processing DataFrame for key: {key}")

    if 'wait_time' not in df.columns:
        print(f"Skipping {key} as 'wait_time' column is missing.")
        continue

    # Skip the first 100 rows
    df = df.iloc[100:] if len(df) > 100 else df

    # Calculate standard deviation
    wait_time_std_dev = df['wait_time'].std()
    std_dev_dict_ooo[key] = wait_time_std_dev

# Plotting the changing standard deviation for all configurations
plt.figure(figsize=(10, 6))
# increase resolution
plt.rcParams['figure.dpi'] = 1000
plt.plot(list(std_dev_dict_ooo.keys()), list(std_dev_dict_ooo.values()), marker='o', linestyle='-', color='blue', label='Standard Deviation')
plt.title('Changing Standard Deviation of Wait Times Across Configurations')
plt.xlabel('Configuration')
plt.ylabel('Standard Deviation (seconds)')
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.xticks(rotation=90, ha='right')
plt.legend()
plt.tight_layout()
plt.savefig(f"{output_dir}/std_dev_across_configurations.png")
plt.show()


Processing DataFrame for key: b128_gpu2_w4
Processing DataFrame for key: b128_gpu2_w8
Processing DataFrame for key: b128_gpu2_w12
Processing DataFrame for key: b128_gpu2_w16
Processing DataFrame for key: b128_gpu2_w20
Processing DataFrame for key: b128_gpu2_w24
Processing DataFrame for key: b128_gpu2_w28
Processing DataFrame for key: b128_gpu3_w4
Processing DataFrame for key: b128_gpu3_w8
Processing DataFrame for key: b128_gpu3_w12
Processing DataFrame for key: b128_gpu3_w16
Processing DataFrame for key: b128_gpu3_w20
Processing DataFrame for key: b128_gpu3_w24
Processing DataFrame for key: b128_gpu3_w28
Processing DataFrame for key: b128_gpu4_w4
Processing DataFrame for key: b128_gpu4_w8
Processing DataFrame for key: b128_gpu4_w12
Processing DataFrame for key: b128_gpu4_w16
Processing DataFrame for key: b128_gpu4_w20
Processing DataFrame for key: b128_gpu4_w24
Processing DataFrame for key: b128_gpu4_w28
Processing DataFrame for key: b256_gpu2_w4
Processing DataFrame for key: b256_gpu2

In [17]:
import os
import matplotlib.pyplot as plt

# Ensure the output directory exists
output_dir = "figs/wait_times"
os.makedirs(output_dir, exist_ok=True)

# # Example structure of df_dict_everything (replace with actual data)
# df_dict_everything = {
#     'config1': pd.DataFrame({'wait_time': [0.5, 0.6, 0.7, 0.8]}),
#     'config2': pd.DataFrame({'wait_time': [0.4, 0.5, 0.6, 0.7]}),
#     'config3': pd.DataFrame({'wait_time': [0.3, 0.4, 0.5, 0.6]}),
# }

# Dictionary to store standard deviation for each configuration
std_dev_dict_io = {}

for key, df in df_dict_everything_io.items():
    print(f"Processing DataFrame for key: {key}")

    if 'wait_time' not in df.columns:
        print(f"Skipping {key} as 'wait_time' column is missing.")
        continue

    # Skip the first 100 rows
    df = df.iloc[100:] if len(df) > 100 else df

    # Calculate standard deviation
    wait_time_std_dev = df['wait_time'].std()
    std_dev_dict_io[key] = wait_time_std_dev

# Plotting the changing standard deviation for all configurations
plt.figure(figsize=(10, 6))
# increase resolution
plt.rcParams['figure.dpi'] = 1000
plt.plot(list(std_dev_dict_io.keys()), list(std_dev_dict_io.values()), marker='o', linestyle='-', color='blue', label='Standard Deviation')
plt.title('Changing Standard Deviation of Wait Times Across Configurations')
plt.xlabel('Configuration')
plt.ylabel('Standard Deviation (seconds)')
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.xticks(rotation=90, ha='right')
plt.legend()
plt.tight_layout()
plt.savefig(f"{output_dir}/std_dev_across_configurations.png")
plt.show()


Processing DataFrame for key: b128_gpu2_w4
Processing DataFrame for key: b128_gpu2_w8
Processing DataFrame for key: b128_gpu2_w12
Processing DataFrame for key: b128_gpu2_w16
Processing DataFrame for key: b128_gpu2_w20
Processing DataFrame for key: b128_gpu2_w24
Processing DataFrame for key: b128_gpu2_w28
Processing DataFrame for key: b128_gpu3_w4
Processing DataFrame for key: b128_gpu3_w8
Processing DataFrame for key: b128_gpu3_w12
Processing DataFrame for key: b128_gpu3_w16
Processing DataFrame for key: b128_gpu3_w20
Processing DataFrame for key: b128_gpu3_w24
Processing DataFrame for key: b128_gpu3_w28
Processing DataFrame for key: b128_gpu4_w4
Processing DataFrame for key: b128_gpu4_w8
Processing DataFrame for key: b128_gpu4_w12
Processing DataFrame for key: b128_gpu4_w16
Processing DataFrame for key: b128_gpu4_w20
Processing DataFrame for key: b128_gpu4_w24
Processing DataFrame for key: b128_gpu4_w28
Processing DataFrame for key: b256_gpu2_w4
Processing DataFrame for key: b256_gpu2

In [21]:
import os
import matplotlib.pyplot as plt

# Ensure the output directory exists
output_dir = "figs/comparison"
os.makedirs(output_dir, exist_ok=True)

# Data from previous calculations
# std_dev_dict_ooo = {'config1': 0.12909944487358058, 'config2': 0.12909944487358055, 'config3': 0.12909944487358055}
# std_dev_dict_io = {'config1': 0.12909944487358058, 'config2': 0.12909944487358058, 'config3': 0.12909944487358055}

std_dev_dict_ooo = {k: v for k, v in std_dev_dict_ooo.items() if 'b512' in k}
std_dev_dict_io = {k: v for k, v in std_dev_dict_io.items() if 'b512' in k}

# Plotting the comparison
plt.figure(figsize=(10, 6))
plt.plot(list(std_dev_dict_ooo.keys()), list(std_dev_dict_ooo.values()), marker='o', linestyle='-', color='blue', label='Original')
plt.plot(list(std_dev_dict_io.keys()), list(std_dev_dict_io.values()), marker='o', linestyle='-', color='red', label='Optimised')
plt.title('Standard Deviation of Batch Wait Times')
plt.xlabel('Configuration')
plt.ylabel('Standard Deviation (seconds)')
plt.grid(axis='y', linestyle='--', alpha=0.7)
plt.xticks(rotation=90, ha='right')
plt.legend()
plt.tight_layout()

# Save and display the plot
plt.savefig(f"{output_dir}/std_dev_across_configurations.png")
plt.show()


In [ ]:
import os
import matplotlib.pyplot as plt

# Ensure the output directory exists
output_dir = "figs/comparisonxxx"
os.makedirs(output_dir, exist_ok=True)

# Calculate queue occupancy time for both runs and store in dicts
queue_occupancy_time_dict_ooo = {}
queue_occupancy_time_dict_io = {}

for key, df in df_dict_everything_ooo.items():
    if 'wait_time' not in df.columns or 'pin_memory_time' not in df.columns:
        continue
    df = df.iloc[100:] if len(df) > 100 else df
    df = df.copy()  # Avoid SettingWithCopyWarning
    df['queue_occupancy_time'] = (
        df['pin_memory_time_ts'] / 1e9
        - df['preprocessing_time_ts'] / 1e9
        - df['preprocessing_time']
    )
    queue_occupancy_time_dict_ooo[key] = df['queue_occupancy_time']

for key, df in df_dict_everything_io.items():
    if 'wait_time' not in df.columns or 'pin_memory_time' not in df.columns:
        continue
    df = df.iloc[100:] if len(df) > 100 else df
    df = df.copy()
    df['queue_occupancy_time'] = (
        df['pin_memory_time_ts'] / 1e9
        - df['preprocessing_time_ts'] / 1e9
        - df['preprocessing_time']
    )
    queue_occupancy_time_dict_io[key] = df['queue_occupancy_time']

# Plot comparison for each key present in either run
all_keys = set(queue_occupancy_time_dict_ooo.keys()) | set(queue_occupancy_time_dict_io.keys())

window = 10

for key in all_keys:
    if 'b512' not in key and 'b1024' not in key:
        continue
    ooo = queue_occupancy_time_dict_ooo.get(key)
    io = queue_occupancy_time_dict_io.get(key)
    if ooo is None or io is None:
        print(f"Skipping {key} as it is missing in one of the runs.")
        continue

    # Align indices (Batch IDs)
    common_index = ooo.index.intersection(io.index)
    ooo = ooo.loc[common_index]
    io = io.loc[common_index]

    # Calculate moving averages
    ooo_ma = ooo.rolling(window=window, min_periods=1).mean()
    io_ma = io.rolling(window=window, min_periods=1).mean()

    plt.figure(figsize=(10, 6))
    # Bar plots (optional: you can comment these out if you want only the lines)
    plt.bar(common_index - 0.2, ooo, width=0.4, color='skyblue', alpha=0.5, label='Original Pipeline')
    plt.bar(common_index + 0.2, io, width=0.4, color='orange', alpha=0.5, label='Optimised Pipeline with Priority Queue')
    # Moving average line plots
    plt.plot(common_index, ooo_ma, color='blue', linewidth=2, label=f'Original Pipeline - Moving Average')
    plt.plot(common_index, io_ma, color='red', linewidth=2, label=f'Optimised Pipeline with Priority Queue - Moving Average')

    plt.title(f'Queue Occupancy Time Comparison for {key}')
    plt.xlabel('Batch ID')
    plt.ylabel('Queue Occupancy Time (seconds)')
    plt.legend()
    plt.grid(axis='y', linestyle='--', alpha=0.7)
    plt.tight_layout()
    plt.savefig(os.path.join(output_dir, f"{key}_queue_occupancy_time_comparison.png"))
    plt.close()
    print(f"Saved plot for {key} in {output_dir}")



Saved plot for b512_gpu4_w28 in figs/comparison
Saved plot for b512_gpu3_w12 in figs/comparison
Saved plot for b1024_gpu2_w16 in figs/comparison
Saved plot for b1024_gpu3_w24 in figs/comparison
Saved plot for b1024_gpu4_w12 in figs/comparison
Saved plot for b1024_gpu2_w20 in figs/comparison
Saved plot for b1024_gpu2_w12 in figs/comparison
Saved plot for b512_gpu2_w12 in figs/comparison
Saved plot for b1024_gpu4_w4 in figs/comparison
Saved plot for b1024_gpu2_w4 in figs/comparison
Saved plot for b512_gpu4_w12 in figs/comparison
Saved plot for b512_gpu3_w8 in figs/comparison
Saved plot for b512_gpu4_w24 in figs/comparison
Saved plot for b512_gpu2_w20 in figs/comparison
Saved plot for b512_gpu4_w8 in figs/comparison
Saved plot for b1024_gpu4_w24 in figs/comparison
Saved plot for b1024_gpu2_w24 in figs/comparison
Saved plot for b1024_gpu3_w8 in figs/comparison
Saved plot for b512_gpu4_w16 in figs/comparison
Saved plot for b1024_gpu3_w28 in figs/comparison
Saved plot for b1024_gpu3_w16 in f

In [10]:
import os
import matplotlib.pyplot as plt

window = 20

# Ensure the output directory exists
output_dir = "figs/comparisonxxx"
os.makedirs(output_dir, exist_ok=True)

def extract_metric_dict(df_dict, metric_name, compute_func=None):
    metric_dict = {}
    for key, df in df_dict.items():
        if 'wait_time' not in df.columns or 'pin_memory_time' not in df.columns:
            continue
        df = df.iloc[100:] if len(df) > 100 else df
        df = df.copy()
        if compute_func:
            df[metric_name] = compute_func(df)
        metric_dict[key] = df[metric_name]
    return metric_dict

# Compute queue occupancy time
def compute_queue_occupancy_time(df):
    return (
        df['pin_memory_time_ts'] / 1e9
        - df['preprocessing_time_ts'] / 1e9
        - df['preprocessing_time']
    )

# Extract metrics for both runs
queue_occupancy_time_dict_ooo = extract_metric_dict(
    df_dict_everything_ooo, 'queue_occupancy_time', compute_queue_occupancy_time
)
queue_occupancy_time_dict_io = extract_metric_dict(
    df_dict_everything_io, 'queue_occupancy_time', compute_queue_occupancy_time
)
wait_time_dict_ooo = extract_metric_dict(df_dict_everything_ooo, 'wait_time')
wait_time_dict_io = extract_metric_dict(df_dict_everything_io, 'wait_time')

def plot_metric_comparison(metric_dict_ooo, metric_dict_io, metric_label, output_dir, window=10):
    all_keys = set(metric_dict_ooo.keys()) | set(metric_dict_io.keys())
    for key in all_keys:
        # if 'b512' not in key and 'b1024' not in key:
            # continue
        ooo = metric_dict_ooo.get(key)
        io = metric_dict_io.get(key)
        if ooo is None or io is None:
            print(f"Skipping {key} as it is missing in one of the runs.")
            continue

        # Align indices (Batch IDs)
        common_index = ooo.index.intersection(io.index)
        print(f"common_index: {common_index}")
        ooo = ooo.loc[common_index]
        io = io.loc[common_index]

        # Calculate moving averages
        ooo_ma = ooo.rolling(window=window, min_periods=1).mean()
        io_ma = io.rolling(window=window, min_periods=1).mean()

        plt.figure(figsize=(10, 6))
        plt.bar(common_index - 0.2, ooo, width=0.4, color='skyblue', alpha=0.5, label='Original Pipeline')
        plt.bar(common_index + 0.2, io, width=0.4, color='orange', alpha=0.5, label='Optimised Pipeline with Priority Queue')
        plt.plot(common_index, ooo_ma, color='blue', linewidth=2, label=f'Original Pipeline - Moving Average')
        plt.plot(common_index, io_ma, color='red', linewidth=2, label=f'Optimised Pipeline with Priority Queue - Moving Average')

        plt.title(f'{metric_label} Comparison for {key}')
        plt.xlabel('Batch ID')
        plt.ylabel(metric_label)
        plt.legend()
        plt.grid(axis='y', linestyle='--', alpha=0.7)
        plt.tight_layout()
        filename = os.path.join(output_dir, f"{key}_{metric_label.replace(' ', '_').lower()}_comparison.png")
        plt.savefig(filename)
        plt.close()
        print(f"Saved plot for {key} ({metric_label}) in {output_dir}")

# Plot both metrics
# plot_metric_comparison(queue_occupancy_time_dict_ooo, queue_occupancy_time_dict_io, "Queue Occupancy Time (seconds)", output_dir)
plot_metric_comparison(wait_time_dict_ooo, wait_time_dict_io, "Batch Wait Time (seconds)", output_dir)


Skipping b256_gpu1_w24 as it is missing in one of the runs.
Skipping b1024_gpu3_w16 as it is missing in one of the runs.
Skipping b1024_gpu3_w12 as it is missing in one of the runs.
Skipping b1024_gpu4_w4 as it is missing in one of the runs.
Skipping b512_gpu3_w8 as it is missing in one of the runs.
Skipping b256_gpu3_w12 as it is missing in one of the runs.
common_index: Index([ 100,  101,  102,  103,  104,  105,  106,  107,  108,  109,
       ...
       2005, 2006, 2007, 2008, 2009, 2010, 2011, 2014, 2015, 2016],
      dtype='int64', name='batch_id', length=1915)
Saved plot for b128_gpu2_w8 (Batch Wait Time (seconds)) in figs/comparisonxxx
Skipping b512_gpu2_w4 as it is missing in one of the runs.
Skipping b1024_gpu3_w4 as it is missing in one of the runs.
Skipping b256_gpu2_w12 as it is missing in one of the runs.
Skipping b512_gpu3_w28 as it is missing in one of the runs.
Skipping b512_gpu2_w20 as it is missing in one of the runs.
Skipping b256_gpu3_w4 as it is missing in one of th